In [2]:
#Import packages
from IPython.display import HTML
import matplotlib.animation as anima
import matplotlib.pyplot as plt
import numpy as np

#Enable notebook for better animation
%matplotlib notebook

In [3]:
#Set up the KdV model
def kdv(x,t,dx):
    up1 = np.hstack([x[1:], x[:1]])
    up2 = np.hstack([x[2:], x[:2]])
    up3 = np.hstack([x[3:], x[:3]])
    up4 = np.hstack([x[4:], x[:4]])
    um1 = np.hstack([x[-1:], x[:-1]])
    um2 = np.hstack([x[-2:], x[:-2]])
    um3 = np.hstack([x[-3:], x[:-3]])
    um4 = np.hstack([x[-4:], x[:-4]])

    #O(h^6) Central differences
    ux1 = ((up3 - um3) - 9 * (up2 - um2) + 45 * (up1 - um1)) / (60 * dx)
    ux3 = (7 * (up4 - um4) - 72 * (up3 - um3) + 338 * (up2 - um2) - 488 * (up1 - um1)) / (240 * dx * dx * dx)
    
    return -6 * x * ux1 - ux3

In [4]:
#Rk4 integration
def rk4(x, dt, dx):
    k1 = dt * kdv(x, 0, dx)
    k2 = dt * kdv(x + k1 * 0.5, 0, dx)
    k3 = dt * kdv(x + k2 * 0.5, 0, dx)
    k4 = dt * kdv(x + k3, 0, dx)
    return x + 1/6. * (k1 + 2*k2 + 2*k3 + k4)

In [5]:
def kdvExact(x,t,v,x0):
    a = np.cosh(0.5 * np.sqrt(v) * (x - v * t - x0))
    return v / (2 * a * a)

In [6]:
dx = 0.1
dt = 1e-4
x = np.arange(-8,8,dx)
y = kdvExact(x,0,16.,0)
accuracy = 2 * dx * dx * dx / (3*np.sqrt(3))

In [7]:
y = kdvExact(x, 0, 16, 4) + kdvExact(x, 0, 4, -4)

In [9]:
fig, ax = plt.subplots()
line, = ax.plot([], [])
ax.set_ylim([-2, 12])
ax.set_xlim([-8, 8])

def init():
    line.set_data([], [])

def animate(i):
    global y
    for i in range(50):
        y = rk4(y, dt, dx)
    line.set_data(x, y)

# N.B. The time elapsed here is going to be (frames * skip)*dt. For dt=1e-4, fames=400 gives 2 seconds.
anim = anima.FuncAnimation(fig, animate, init_func=init, frames=400, interval = 20, repeat=False) 

plt.close()

HTML(anim.to_jshtml())

<IPython.core.display.Javascript object>